<a href="https://colab.research.google.com/github/rsn870/DCGAN/blob/master/DCGAN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:

import torch
import torch.nn as nn
import torchvision
from torchvision import transforms , datasets
from torch.utils.data import DataLoader
import torch.optim as optim
from tqdm import  tqdm 
import matplotlib.pyplot as plt
import numpy as np
import torchvision.utils as utils 
%matplotlib inline
import matplotlib.pyplot as plt 

In [2]:
import numpy
from numpy import cov
from numpy import trace
from numpy import iscomplexobj
from numpy import asarray
from numpy.random import randint
from scipy.linalg import sqrtm
from keras.applications.inception_v3 import InceptionV3
from keras.applications.inception_v3 import preprocess_input
from keras.datasets.mnist import load_data
from skimage.transform import resize
 
# scale an array of images to a new size
def scale_images(images, new_shape):
	images_list = list()
	for image in images:
		# resize with nearest neighbor interpolation
		new_image = resize(image, new_shape, 0)
		# store
		images_list.append(new_image)
	return asarray(images_list)
 
# calculate frechet inception distance
def calculate_fid(model, images1, images2):
	# calculate activations
	act1 = model.predict(images1)
	act2 = model.predict(images2)
	# calculate mean and covariance statistics
	mu1, sigma1 = act1.mean(axis=0), cov(act1, rowvar=False)
	mu2, sigma2 = act2.mean(axis=0), cov(act2, rowvar=False)
	# calculate sum squared difference between means
	ssdiff = numpy.sum((mu1 - mu2)**2.0)
	# calculate sqrt of product between cov
	covmean = sqrtm(sigma1.dot(sigma2))
	# check and correct imaginary numbers from sqrt
	if iscomplexobj(covmean):
		covmean = covmean.real
	# calculate score
	fid = ssdiff + trace(sigma1 + sigma2 - 2.0 * covmean)
	return fid
 
# prepare the inception v3 model
model = InceptionV3(include_top=False, pooling='avg', input_shape=(299,299,3))

#code snippet for FID has been adapted from : https://machinelearningmastery.com/how-to-implement-the-frechet-inception-distance-fid-from-scratch/

Using TensorFlow backend.


87916544/87910968 [==============================] - 1s 0us/step


In [0]:
transform = transforms.Compose(
    [transforms.Resize((64,64)) , transforms.ToTensor(),
     transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])

trainset = datasets.CIFAR10(root='./data', train=True,
                                        download=True, transform=transform)
trainloader = DataLoader(trainset, batch_size=4,
                                          shuffle=True, num_workers=2)

testset = datasets.CIFAR10(root='./data', train=False,
                                       download=True, transform=transform)
testloader = DataLoader(testset, batch_size=4,
                                         shuffle=False, num_workers=2)

classes = ('plane', 'car', 'bird', 'cat',
           'deer', 'dog', 'frog', 'horse', 'ship', 'truck')


Extracting ./data/cifar-10-python.tar.gz to ./data
Files already downloaded and verified


In [0]:

dataiter = iter(trainloader)
images, labels = dataiter.next()


if torch.cuda.is_available() :
  device = torch.device("cuda:0")
else :
  device = "cpu"

In [0]:
nz = 10
nc = 3
ngf = 2
ndf = 2

In [0]:
class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()
        #self.ngpu = ngpu
        self.main = nn.Sequential(
            # input is Z, going into a convolution
            nn.ConvTranspose2d(nz, ngf * 8, 4, 1, 0, bias=False),
            nn.BatchNorm2d(ngf * 8),
            nn.ReLU(True),
            # state size. (ngf*8) x 4 x 4
            nn.ConvTranspose2d(ngf * 8, ngf * 4, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf * 4),
            nn.ReLU(True),
            # state size. (ngf*4) x 8 x 8
            nn.ConvTranspose2d(ngf * 4, ngf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf * 2),
            nn.ReLU(True),
            # state size. (ngf*2) x 16 x 16
            nn.ConvTranspose2d(ngf * 2,ngf, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf),
            nn.ReLU(True),
            # state size. (ngf) x 32 x 32
            nn.ConvTranspose2d(ngf,nc, 4, 2, 1, bias=False),
            nn.Tanh()
            # state size. (nc) x 64 x 64
        )

    def forward(self , x) :

      output = self.main(x)

      return output

    
     

In [0]:
   
class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()
        #self.ngpu = ngpu
        self.main = nn.Sequential(
            # input is (nc) x 64 x 64
            nn.Conv2d(nc, ndf, 4, 2, 1, bias=False),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf) x 32 x 32
            nn.Conv2d(ndf, ndf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 2),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*2) x 16 x 16
            nn.Conv2d(ndf * 2, ndf * 4, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 4),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*4) x 8 x 8
            nn.Conv2d(ndf * 4, ndf * 8, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 8),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*8) x 4 x 4
            nn.Conv2d(ndf * 8, 1, 4, 1, 0, bias=False),
            nn.Sigmoid()
        )

    def forward(self, x):

      output = self.main(x)
      return output.view(-1, 1).squeeze(1)
      

    

In [0]:
def weights_init(m):
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        m.weight.data.normal_(0.0, 0.02)
    elif classname.find('BatchNorm') != -1:
        m.weight.data.normal_(1.0, 0.02)
        m.bias.data.fill_(0)


In [0]:

netG = Generator()
netG = netG.to(device)
netG.apply(weights_init)



Generator(
  (main): Sequential(
    (0): ConvTranspose2d(10, 16, kernel_size=(4, 4), stride=(1, 1), bias=False)
    (1): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (2): ReLU(inplace=True)
    (3): ConvTranspose2d(16, 8, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (4): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (5): ReLU(inplace=True)
    (6): ConvTranspose2d(8, 4, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (7): BatchNorm2d(4, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (8): ReLU(inplace=True)
    (9): ConvTranspose2d(4, 2, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (10): BatchNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (11): ReLU(inplace=True)
    (12): ConvTranspose2d(2, 3, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (13): Tanh()
  )
)

In [0]:

netD = Discriminator()
netD = netD.to(device)
netD.apply(weights_init)

Discriminator(
  (main): Sequential(
    (0): Conv2d(3, 2, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (1): LeakyReLU(negative_slope=0.2, inplace=True)
    (2): Conv2d(2, 4, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (3): BatchNorm2d(4, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (4): LeakyReLU(negative_slope=0.2, inplace=True)
    (5): Conv2d(4, 8, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (6): BatchNorm2d(8, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (7): LeakyReLU(negative_slope=0.2, inplace=True)
    (8): Conv2d(8, 16, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
    (9): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (10): LeakyReLU(negative_slope=0.2, inplace=True)
    (11): Conv2d(16, 1, kernel_size=(4, 4), stride=(1, 1), bias=False)
    (12): Sigmoid()
  )
)

In [0]:
fixed_noise = torch.randn(4, nz, 1, 1, device=device)

G_solver = optim.Adam(netG.parameters(), lr=0.01)
D_solver = optim.Adam(netD.parameters(), lr=0.01)

In [0]:
for epoch in tqdm(range(18000)):
   for i, data in enumerate(trainloader, 0):
        ############################
        # (1) Update D network: maximize log(D(x)) + log(1 - D(G(z)))
        ###########################
        # train with real
        netD.zero_grad()
        real_cpu = data[0].to(device)
        batch_size = real_cpu.size(0)
        D_real = netD(real_cpu)

        D_x = D_real.mean().item()

        noise = torch.randn(batch_size, nz, 1, 1, device=device)
        fake = netG(noise)

        D_fake = netD(fake)

        D_G_z1 = D_fake.mean().item()

        D_loss = -(torch.mean(D_real) - torch.mean(D_fake))

        D_loss.backward(retain_graph= True) 
        D_solver.step() 

        
        for p in netD.parameters():
            p.data.clamp_(-0.01, 0.01)

        netD.zero_grad()
        netG.zero_grad()

        output = netD(fake)
        D_G_z2 = output.mean().item()
        G_loss = -torch.mean(output)
        G_loss.backward(retain_graph= True)
        G_solver.step()

        print('[%d/%d][%d/%d] Loss_D: %.4f Loss_G: %.4f D(x): %.4f D(G(z)): %.4f / %.4f' % (epoch, 18000, i, len(trainloader),
                 D_loss.item(), G_loss.item(), D_x, D_G_z1, D_G_z2))
        
        if i % 100 == 0:
            fake = netG(fixed_noise)

            fake = fake.cpu().numpy()

            fig=plt.figure(figsize=(8, 8))
            columns = 4
            rows = 5
            for i in range(1, columns*rows +1):
              img = fake[i-1]
              fig.add_subplot(rows, columns, i)
              plt.imshow(img)
           
           plt.show()  

        if i % 1000 == 0 :
          real = real_cpu.cpu().numpy()
          fake = netG(fixed_noise)
          fake = fake.cpu().numpy()
          images1 = real
          images2 = fake 

          images1 = scale_images(images1, (299,299,3))
          images2 = scale_images(images2, (299,299,3))

          images1 = preprocess_input(images1)
          images2 = preprocess_input(images2)

          fid = calculate_fid(model , images1 , images2)

          print('FID (different): %.3f' % fid)


          


          







             
           
          

        
         
          

        
        
        





     
      

     


     
      

   





  0%|          | 0/1000 [00:00<?, ?it/s]

Streaming output truncated to the last 5000 lines.
[0/1000][7501/12500] Loss_D: -0.0012 Loss_G: -0.4988 D(x): 0.5000 D(G(z)): 0.4989 / 0.4988
[0/1000][7502/12500] Loss_D: -0.0020 Loss_G: -0.4986 D(x): 0.5010 D(G(z)): 0.4990 / 0.4986
[0/1000][7503/12500] Loss_D: -0.0019 Loss_G: -0.4986 D(x): 0.5005 D(G(z)): 0.4986 / 0.4986
[0/1000][7504/12500] Loss_D: -0.0018 Loss_G: -0.4988 D(x): 0.5005 D(G(z)): 0.4987 / 0.4988
[0/1000][7505/12500] Loss_D: -0.0014 Loss_G: -0.4981 D(x): 0.4995 D(G(z)): 0.4981 / 0.4981
[0/1000][7506/12500] Loss_D: -0.0014 Loss_G: -0.4987 D(x): 0.5001 D(G(z)): 0.4987 / 0.4987
[0/1000][7507/12500] Loss_D: -0.0019 Loss_G: -0.4986 D(x): 0.5007 D(G(z)): 0.4988 / 0.4986
[0/1000][7508/12500] Loss_D: -0.0019 Loss_G: -0.4985 D(x): 0.5004 D(G(z)): 0.4986 / 0.4985
[0/1000][7509/12500] Loss_D: -0.0001 Loss_G: -0.4985 D(x): 0.4986 D(G(z)): 0.4986 / 0.4985
[0/1000][7510/12500] Loss_D: -0.0013 Loss_G: -0.4986 D(x): 0.5002 D(G(z)): 0.4988 / 0.4986
[0/1000][7511/12500] Loss_D: -0.0013 Lo

  0%|          | 1/1000 [04:09<69:21:01, 249.91s/it]

Streaming output truncated to the last 5000 lines.
[1/1000][7497/12500] Loss_D: -0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7498/12500] Loss_D: -0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7499/12500] Loss_D: 0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7500/12500] Loss_D: 0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7501/12500] Loss_D: -0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7502/12500] Loss_D: -0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7503/12500] Loss_D: -0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7504/12500] Loss_D: 0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7505/12500] Loss_D: -0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7506/12500] Loss_D: 0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5000 / 0.5000
[1/1000][7507/12500] Loss_D: -0.0000 Loss_G

  0%|          | 2/1000 [08:21<69:24:41, 250.38s/it]

...

  1%|          | 7/1000 [29:26<69:36:35, 252.36s/it]

Streaming output truncated to the last 5000 lines.
[7/1000][7497/12500] Loss_D: 0.0000 Loss_G: -0.4999 D(x): 0.4999 D(G(z)): 0.4999 / 0.4999
[7/1000][7498/12500] Loss_D: -0.0001 Loss_G: -0.5000 D(x): 0.5001 D(G(z)): 0.5000 / 0.5000
[7/1000][7499/12500] Loss_D: 0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5001 / 0.5000
[7/1000][7500/12500] Loss_D: -0.0001 Loss_G: -0.5001 D(x): 0.5001 D(G(z)): 0.5001 / 0.5001
[7/1000][7501/12500] Loss_D: -0.0001 Loss_G: -0.5000 D(x): 0.5002 D(G(z)): 0.5001 / 0.5000
[7/1000][7502/12500] Loss_D: -0.0003 Loss_G: -0.4998 D(x): 0.5002 D(G(z)): 0.5000 / 0.4998
[7/1000][7503/12500] Loss_D: -0.0000 Loss_G: -0.5000 D(x): 0.5001 D(G(z)): 0.5000 / 0.5000
[7/1000][7504/12500] Loss_D: 0.0002 Loss_G: -0.5000 D(x): 0.4998 D(G(z)): 0.5000 / 0.5000
[7/1000][7505/12500] Loss_D: 0.0001 Loss_G: -0.4999 D(x): 0.5000 D(G(z)): 0.5000 / 0.4999
[7/1000][7506/12500] Loss_D: 0.0000 Loss_G: -0.5000 D(x): 0.5000 D(G(z)): 0.5001 / 0.5000
[7/1000][7507/12500] Loss_D: 0.0000 Loss_G: 

  1%|          | 8/1000 [33:43<69:56:15, 253.81s/it]

Streaming output truncated to the last 5000 lines.
[8/1000][5637/12500] Loss_D: -0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5638/12500] Loss_D: -0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5639/12500] Loss_D: -0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5640/12500] Loss_D: 0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5641/12500] Loss_D: -0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5642/12500] Loss_D: 0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5643/12500] Loss_D: 0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5644/12500] Loss_D: -0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5645/12500] Loss_D: -0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5646/12500] Loss_D: -0.0000 Loss_G: -0.5002 D(x): 0.5002 D(G(z)): 0.5002 / 0.5002
[8/1000][5647/12500] Loss_D: 0.0000 Loss_G

KeyboardInterrupt: ignored